In [59]:
import nltk
import re
import numpy as np


In [60]:
import datasets

# Load the dataset
dataset = datasets.load_dataset("GEM/xlsum", "arabic")

# Print the dataset info
print(dataset)

Found cached dataset xlsum (C:/Users/DELL/.cache/huggingface/datasets/GEM___xlsum/arabic/2.0.0/eb0c1bd988fe61962620fe73722ebc91e0fd5729b4c8acbf3e3b3c50f8b22a96)


  0%|          | 0/3 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['gem_id', 'url', 'title', 'target', 'references', 'text'],
        num_rows: 37519
    })
    test: Dataset({
        features: ['gem_id', 'url', 'title', 'target', 'references', 'text'],
        num_rows: 4689
    })
    validation: Dataset({
        features: ['gem_id', 'url', 'title', 'target', 'references', 'text'],
        num_rows: 4689
    })
})


In [61]:
for i in range(5):
    print(dataset["train"][i])

{'gem_id': 'xlsum_arabic-train-1', 'url': 'https://www.bbc.com/arabic/worldnews/2014/03/140323_russian_troops_crimea_naval_base', 'title': 'القوات الأوكرانية تبدأ الانسحاب من القرم', 'target': 'بدأت القوات الأوكرانية الانسحاب من شبه جزيرة القرم. \n\n', 'references': ['بدأت القوات الأوكرانية الانسحاب من شبه جزيرة القرم. \n\n'], 'text': 'وكان الرئيس الأوكراني المؤقت، الكسندر تورتشينوف، قد أمر بسحب جميع القوات الأوكرانية من القرم.\n\nوسيطرت قوات روسية صباح الاثنين على قاعدة بحرية أوكرانية في فيودوسيا، في ثالث هجوم من نوعه خلال 48 ساعة، وذلك بحسب تصريحات مسؤولين أوكرانيين لبي بي سي .\n\nوقال المتحدث باسم وزارة الدفاع الأوكرانية فلاديسلاف سيليزنيوف إن القوات الروسية هاجمت القاعدة وألقت القبض على الجنود الأوكرانيين في قاعدة فيودوسيا وقيدت أيادي ضباطهم.\n\nومن المتوقع أن تسيطر الأزمة الأوكرانية على قمة مجموعة الدول الصناعية السبع في لاهاي.\n\nمواضيع قد تهمك نهاية\n\nوأكد الرئيس الأمريكي باراك أوباما خلال لقاء مع نظيره الصيني شى جين بينغ على أن "واشنطن وبكين يمكنهما، بالعمل سويا، تعزيز القانون

In [62]:
import pandas as pd

In [63]:
train_inputs = dataset['train']['text']
train_labels = dataset['train']['target']


In [64]:
train_inputs = pd.DataFrame(train_inputs)
train_labels = pd.DataFrame(train_labels)
# Print the shape of the inputs and labels
print("Train inputs shape:", train_inputs.shape)
print("Train labels shape:", train_labels.shape)

Train inputs shape: (37519, 1)
Train labels shape: (37519, 1)


## Text Cleaning

### Analyze text by checking if it has any punctuation symbols

In [65]:
punctuations= ['?',':','!','.',',',';','؟','؛','،','(',')','/','"','-','\\', '\n', '#']

# Function to count occurrences of punctuations in a given sentence
def count_punctuations(sentence):
    return sum([sentence.count(p) for p in punctuations])

# Add new column with punctuation counts for each sentence
train_inputs['Punctuation_Counts'] = train_inputs[0].apply(count_punctuations)
train_labels['Punctuation_Counts'] = train_labels[0].apply(count_punctuations)

# Calculate total punctuation count for all sentences in DataFrame
total_punctuation_count_train = train_inputs['Punctuation_Counts'].sum()
total_punctuation_count_label = train_labels['Punctuation_Counts'].sum()


# Print total punctuation count
print(f'Total Training Punctuation Count: {total_punctuation_count_train}')
print(f'Total Label Punctuation Count: {total_punctuation_count_label}')

Total Training Punctuation Count: 3608661
Total Label Punctuation Count: 115659


### Normalize by removing all punctuations

In [66]:

replace_punc = lambda x: ''.join([' ' if ch in punctuations else ch for ch in x])
train_inputs.iloc[:, 0] = train_inputs.iloc[:, 0].apply(replace_punc)
train_labels.iloc[:, 0] = train_labels.iloc[:, 0].apply(replace_punc)


In [67]:
# Calculate total punctuation count for all sentences in DataFrame
total_punctuation_count_train = train_inputs['Punctuation_Counts'].sum()
total_punctuation_count_label = train_labels['Punctuation_Counts'].sum()


# Print total punctuation count
print(f'Total Training Punctuation Count: {total_punctuation_count_train}')
print(f'Total Label Punctuation Count: {total_punctuation_count_label}')

Total Training Punctuation Count: 3608661
Total Label Punctuation Count: 115659


### Normalize by replacing 'ta2 marboota' with 'ha2 marboota' and 'ya2' with 'ya2 mankoota'

In [68]:
replace_ha2_marboota = lambda x: ''.join(['ه' if ch == 'ة' else ch for ch in x])
replace_ya2 = lambda x: ''.join(['ي' if ch == 'ى' else ch for ch in x])
train_inputs.iloc[:,0] = train_inputs.iloc[:,0].apply(replace_ha2_marboota)
train_labels.iloc[:,0] = train_labels.iloc[:,0].apply(replace_ha2_marboota)
train_inputs.iloc[:,0] = train_inputs.iloc[:,0].apply(replace_ya2)
train_labels.iloc[:,0] = train_labels.iloc[:,0].apply(replace_ya2)


In [69]:
print(train_inputs[0][0])
print(train_labels[0][0])

وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينوف  قد أمر بسحب جميع القوات الأوكرانيه من القرم   وسيطرت قوات روسيه صباح الاثنين علي قاعده بحريه أوكرانيه في فيودوسيا  في ثالث هجوم من نوعه خلال 48 ساعه  وذلك بحسب تصريحات مسؤولين أوكرانيين لبي بي سي    وقال المتحدث باسم وزاره الدفاع الأوكرانيه فلاديسلاف سيليزنيوف إن القوات الروسيه هاجمت القاعده وألقت القبض علي الجنود الأوكرانيين في قاعده فيودوسيا وقيدت أيادي ضباطهم   ومن المتوقع أن تسيطر الأزمه الأوكرانيه علي قمه مجموعه الدول الصناعيه السبع في لاهاي   مواضيع قد تهمك نهايه  وأكد الرئيس الأمريكي باراك أوباما خلال لقاء مع نظيره الصيني شي جين بينغ علي أن  واشنطن وبكين يمكنهما  بالعمل سويا  تعزيز القانون الدولي واحترام سياده الدول    وتسيطر قوات روسيه حاليا علي معظم القواعد العسكريه الأوكرانيه في القرم التي أعلنت موسكو ضمها للاتحاد الروسي بعد استفتاء أجرته السلطات المحليه هناك   قلق بالغ  وقال مارك لوين  مراسل بي بي سي في القرم  إن القوات الروسيه تسيطر بشكل كامل علي القاعده  ونقلت الجنود الأوكرانيين بعيدا إلي مكان مجهول   وتعد قاعده فيودوسيا واح

In [70]:
train_inputs[0]

0        وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...
1        بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...
2        وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...
3        ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...
4        مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...
                               ...                        
37514    يثور بركان بولسكي تولباشيك شرقي روسيا منذ نوفم...
37515    بينما احتدمت أزمه احتجاز الرهائن علي يد لاجئ إ...
37516    رمضان آخر يستقبله المسلمون في ظل كورونا  للعام...
37517    بعض الأصوات المؤيده للنظم العربيه استغلت اقتحا...
37518    تزامنا مع الذكري التسعين لاكتشاف مقبره توت عنخ...
Name: 0, Length: 37519, dtype: object

### Analyze by check if the text has any diacritics, If so remove them

In [71]:

# Regular expression to match diacritics in Arabic text
diacritic_pattern = re.compile('[\u064B-\u065F\u0670]')

# Function to count diacritics in a given sentence
def count_diacritics(sentence):
    return len(re.findall(diacritic_pattern, sentence))

# Add new column with diacritic counts for each sentence
train_inputs['Diacritic_Counts'] = train_inputs[0].apply(count_diacritics)
train_labels['Diacritic_Counts'] = train_labels[0].apply(count_diacritics)

# Calculate total diacritic count for all sentences in DataFrame
total_train_diacritic_count = train_inputs['Diacritic_Counts'].sum()
total_label_diacritic_count = train_labels['Diacritic_Counts'].sum()


print(f'Total Training Diacritic Count: {total_train_diacritic_count}')
print(f'Total Lebels Diacritic Count: {total_label_diacritic_count}')



Total Training Diacritic Count: 152867
Total Lebels Diacritic Count: 5966


### Normalize by removing all diacritics and non-arabic words

In [72]:
# Define a regular expression to match diacritics
diacritics_pattern = re.compile("[ًٌٍَُِّْ]")

# Define a regular expression to match non-Arabic characters
non_arabic_pattern = re.compile("[^\u0600-\u06FF ]")

# Define a function to preprocess the text data
def preprocess_text(text):
    # Remove diacritics from the text
    text = diacritics_pattern.sub("", text)

    # Remove non-Arabic characters from the text
    text = non_arabic_pattern.sub("", text)

    # Remove Arabic punctuations from the text
    text = ''.join([' ' if ch in punctuations else ch for ch in text])

    return text

# Preprocess the input data
train_inputs['cleaned_text'] = train_inputs[0].apply(preprocess_text)
train_labels['cleaned_text'] = train_labels[0].apply(preprocess_text)

In [73]:
# Calculate total diacritic count for all sentences in DataFrame
total_train_diacritic_count = train_inputs['cleaned_text'].apply(count_diacritics).sum()
total_label_diacritic_count = train_labels['cleaned_text'].apply(count_diacritics).sum()


print(f'Total Training Diacritic Count: {total_train_diacritic_count}')
print(f'Total Lebels Diacritic Count: {total_label_diacritic_count}')

Total Training Diacritic Count: 0
Total Lebels Diacritic Count: 0


In [74]:
train_inputs = train_inputs.rename(columns={0: 'original_Text'})
train_labels = train_labels.rename(columns={0: 'original_Text'})
train_inputs.head()

original_Text  Punctuation_Counts  \
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...                 125   
1  بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...                  70   
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...                  35   
3  ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...                 284   
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...                  25   

   Diacritic_Counts                                       cleaned_text  
0                 0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...  
1                 1  بحلول عام  ستحتاج مصر إلي  مليار متر مكعب فوق ...  
2                 0  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...  
3                15  ووقع اختياره علي واد عمقه  متر محاط بثماني قمم...  
4                 3  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...

In [75]:
all_text = ' '.join(train_inputs['cleaned_text'])

# Split the string into words and get the unique words
unique_words = set(all_text.split())

# Print the unique words
print(unique_words)

{'ماغويرك', 'ناحيهأخري', 'يرغبونها', 'ملحمي', 'مردفا', 'بمحنه', 'هاو', 'التبحر', 'وسلطويه', 'بتشكيله', 'تصرخين', 'فتيء', 'وسلطان', 'بمناشده', 'بأبعادها', 'فاستبدله', 'أدله', 'بينغل', 'تشيرابونجي', 'أتفهمه', 'لمادتي', 'فمزارع', 'أصحح', 'والحشائس', 'عنهاكما', 'لزوارمنطقه', 'وتكابد', 'حصولي', 'وآرت', 'اشيد', 'والسماء', 'خاله', 'متناقضا', 'الانعزال', 'الميتوكوندريا', 'وميرسيسايد', 'قعرها', 'ومآثره', 'آمو', 'سينذر', 'للمهتمين', 'بداح', 'والخناجر', 'وعبدالمهدي', 'وأوجد', 'وابنائي', 'انطلاقتها', 'والمزايدين', 'والعقلي', 'واستديو', 'المهانين', 'كوتاي', 'التأملي', 'للتوثيق', 'تدابي', 'بدانتهم', 'والآلات', 'تعسه', 'بالاسباني', 'ثقلها', 'نتحسر', 'فالكتب', 'بخدماتهم', 'والتشاديين', 'جرته', 'خارجها', 'بقسوه', 'غريام', 'وسيردي', 'ارتكبوها', 'الأسطوري', 'واعتياد', 'أولايا', 'وينتظرونه', 'وحاسبوه', 'وجدلا', 'وإنذار', 'كثيرين', 'بتسجيلات', 'بتفاعل', 'السبعينيه', 'الرعوي', 'فالملا', 'فقراتين', 'أندرتون', 'نلحظ', 'بارغن', 'الغائه', 'طائرهم', 'محدثين', 'ساوند', 'استنكارها', 'اصبعو', 'وزناني', 'والرشاوي', 

In [76]:
print(len(list(unique_words)))

337948


In [77]:
train_inputs.head()

original_Text  Punctuation_Counts  \
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...                 125   
1  بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...                  70   
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...                  35   
3  ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...                 284   
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...                  25   

   Diacritic_Counts                                       cleaned_text  
0                 0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...  
1                 1  بحلول عام  ستحتاج مصر إلي  مليار متر مكعب فوق ...  
2                 0  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...  
3                15  ووقع اختياره علي واد عمقه  متر محاط بثماني قمم...  
4                 3  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...

## Text Tokenization

In [78]:
nltk.download('punkt')
# Define a function to tokenize the text data
def tokenize(text):
    # Tokenize the text using the Arabic word tokenizer from the nltk library
    tokens = nltk.word_tokenize(text)

    # Split any multi-word tokens into separate tokens
    new_tokens = []
    for token in tokens:
        if ' ' in token:
            subtokens = nltk.word_tokenize(token)
            new_tokens.extend(subtokens)
        else:
            new_tokens.append(token)
    return new_tokens
# train_inputs_labels = pd.DataFrame([])
train_inputs['tokens'] = train_inputs['cleaned_text'].apply(tokenize)
train_labels['tokens'] = train_labels['cleaned_text'].apply(tokenize)




[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [79]:
train_inputs.head()

original_Text  Punctuation_Counts  \
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...                 125   
1  بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...                  70   
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...                  35   
3  ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...                 284   
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...                  25   

   Diacritic_Counts                                       cleaned_text  \
0                 0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...   
1                 1  بحلول عام  ستحتاج مصر إلي  مليار متر مكعب فوق ...   
2                 0  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...   
3                15  ووقع اختياره علي واد عمقه  متر محاط بثماني قمم...   
4                 3  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...   

                                              tokens  
0  [وكان, الرئيس, الأوكراني, المؤقت, الكسندر, تور...  
1  [بحلول, عام, ستحتاج, مصر, إلي, مليار, متر, مكع...  
2  [وذكرت, وكاله, الأنباء, المحليه, جي, إن, إس, أ...  
3  [ووقع, اختياره, علي, واد, عمقه, متر, محاط, بثم...  
4  [مسلح, حوثي, في, إب, وقال, المصدر, إن, المسلحي...

In [80]:
# Get the unique tokens in all articles
unique_tokens = pd.Series(train_inputs['tokens'].explode().unique())

# Preview the unique tokens
print(unique_tokens)

0              وكان
1            الرئيس
2         الأوكراني
3            المؤقت
4           الكسندر
            ...    
337943      للتنفير
337944        تأبيد
337945       لايؤشر
337946     هيلتوفير
337947        فكتوم
Length: 337948, dtype: object


## Removing stop words

### We will remove stop words to ease the training process

In [81]:
def remove_stop_words(tokens):
    filtered_tokens = [token for token in tokens if token not in stop_words]
    return filtered_tokens
train_inputs['tokens'] = train_inputs['tokens'].apply(remove_stop_words)

In [82]:
# Get the unique tokens in all articles
unique_tokens = pd.Series(train_inputs['tokens'].explode().unique())

# Preview the unique tokens
print(unique_tokens)

0              وكان
1            الرئيس
2         الأوكراني
3            المؤقت
4           الكسندر
            ...    
337460      للتنفير
337461        تأبيد
337462       لايؤشر
337463     هيلتوفير
337464        فكتوم
Length: 337465, dtype: object


### Note how the number of unique tokens in the training data was reduced from 337947 before removing stop words to 337464 after removing stop words

In [20]:
# from nltk.stem.isri import ISRIStemmer
# # Create an instance of the ISRI Arabic stemmer
# stemmer = ISRIStemmer()

# # Define a function to apply stemming to a list of tokens
# def stem_tokens(tokens):
#     stemmed_tokens = []
#     for token in tokens:
#         stemmed_token = stemmer.stem(token)
#         stemmed_tokens.append(stemmed_token)
#     return stemmed_tokens

# train_inputs['stemmed_tokens'] = train_inputs['tokens'].apply(stem_tokens)


## Lemmatizing tokens

In [83]:
from nltk.stem.isri import ISRIStemmer
def lemmatize_tokens(tokens):
    lemmatized_tokens = []
    for token in tokens:
        lemmatized_token = ISRIStemmer().suf32(token)
        lemmatized_tokens.append(lemmatized_token)
    return lemmatized_tokens

train_inputs['lemmatized_tokens'] = train_inputs['tokens'].apply(lemmatize_tokens)


In [84]:
train_inputs['lemmatized_tokens'][2]

['وذكرت',
 'وكاله',
 'الأنباء',
 'المحليه',
 'جي',
 'إس',
 'جماعه',
 'جيش',
 'محمد',
 'المتشدده',
 'أعلنت',
 'مسؤوليت',
 'الهجوم',
 'منطقه',
 'كشمير',
 'المتنازع',
 'علي',
 'الهند',
 'وباكس',
 'خلال',
 'العقود',
 'الست',
 'الماضيه',
 'ظلت',
 'منطقه',
 'كشمير',
 'القريبه',
 'جبال',
 'الهيمالا',
 'محل',
 'نزاع',
 'الهند',
 'وباكس',
 'الجنه',
 'الملعونه',
 'دموع',
 'الفقراء',
 'كشمير',
 'لماذا',
 'يلجأ',
 'الناس',
 'إلي',
 'أضرحه',
 'الصوفي',
 'كشمير',
 'الهنديه',
 'بالصور',
 'الطفوله',
 'المسروقه',
 'كشمير',
 'فمنذ',
 'تقسيم',
 'الهند',
 'وقيام',
 'باكس',
 'عام',
 'وقعت',
 'حرب',
 'البلد',
 'حول',
 'منطقه',
 'كشمير',
 'الأغلبيه',
 'المسلمه',
 'والتي',
 'يطالب',
 'البلد',
 'بالسياده',
 'علي',
 'وتعد',
 'كشمير',
 'اليوم',
 'واحده',
 'المناطق',
 'المدججه',
 'بالسلاح',
 'العالم',
 'تدير',
 'الص',
 'أجزاء',
 'الإقليم',
 'تسلسل',
 'زمني',
 'لأهم',
 'الأحداث',
 'كشمير']

## Load BERT Arabic for words embeddings

In [73]:
from transformers import AutoTokenizer, AutoModel

# load pre-trained tokenizer and model for Arabic
tokenizer = AutoTokenizer.from_pretrained("asafaya/bert-base-arabic")
model = AutoModel.from_pretrained("asafaya/bert-base-arabic")

# get embeddings for each token
tokens = ['هذا', 'هو', 'بيت', 'و', 'ذهب', 'إلى', 'سوق']
inputs = tokenizer(tokens, return_tensors="pt", padding=True, truncation=True)
outputs = model(**inputs)

embeddings = outputs.last_hidden_state.mean(dim=1).detach()

print(embeddings.tolist())


Some weights of the model checkpoint at asafaya/bert-base-arabic were not used when initializing BertModel: ['cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


7


In [76]:
def generate_embeddings(tokens):
    embeddings = []
    inputs = tokenizer(tokens, return_tensors="pt", padding=True, truncation=True)
    outputs = model(**inputs)
    embeddings = outputs.last_hidden_state.mean(dim=1).detach()
    return embeddings.tolist()

train_inputs['embeddings'] = train_inputs['lemmatized_tokens'].apply(generate_embeddings)

KeyboardInterrupt: 